In [17]:
import os, sys, copy, sumolib, json, datetime
import pandas as pd
import numpy as np

In [18]:
class DailyPreprocessor():
    def __init__(self):
        pass
self = DailyPreprocessor()

In [19]:
# 루트폴더 지정
self.path_root = os.path.dirname(os.path.dirname(os.path.join(os.path.abspath('.'))))
print(self.path_root)

with open(os.path.join(self.path_root, 'configs', 'config.json'), 'r') as file:
    config = json.load(file)

# 주요 폴더 경로 지정
self.paths = config['paths']
self.path_data = os.path.join(self.path_root, *self.paths['data'])
self.path_intermediates = os.path.join(self.path_root, *self.paths['intermediates'])
self.path_results = os.path.join(self.path_root, *self.paths['results'])
self.path_tables = os.path.join(self.path_root, *self.paths['tables'])
self.path_networks = os.path.join(self.path_root, *self.paths['networks'])
self.path_scripts = os.path.join(self.path_root, *self.paths['scripts'])
print(self.path_data)
print(self.path_intermediates)
print(self.path_results)
print(self.path_tables)
print(self.path_networks)
print(self.path_scripts)

c:\Github\snits_siggen
c:\Github\snits_siggen\Data
c:\Github\snits_siggen\Intermediates
c:\Github\snits_siggen\Results
c:\Github\snits_siggen\Data\tables
c:\Github\snits_siggen\Data\networks
c:\Github\snits_siggen\Scripts


In [20]:
# 1-1. 네트워크 불러오기
self.net = sumolib.net.readNet(os.path.join(self.path_networks, 'sn.net.xml'))

In [21]:
# 1-2. 테이블 불러오기
self.alphs = ['A', 'B']

loading_dtype_1 = {'CRSRD_ID':int,          'CRSRD_NM':str,          'CRSRD_TYPE':int,        
                   'CTRLER_TYPE':str,       'CYCL':int,              'DAY':int,               
                   'FLOW_NO':int,           'FRI_PLAN_NO':int,       'FRST_REG_DT':str,       
                   'GRP_NO':int,            'HOUR':int,              'LAST_MDFCN_DT':str,     
                   'LGTD':float,            'LOS_YN':int,            'LTTD':float,            
                   'MAIN_CRSRD_ID':str,     'MAIN_PHASE':int,        'MIN':int,               
                   'MNTH':int,              'MON_PLAN_NO':int,       'NODE_ID':str,           
                   'OFFSET':int,            'PHASE':int,             'PHASE_DT':str,          
                   'PLAN_NO':int,           'PPC_TYPE':int,          'RING':str,              
                   'RINGA_FLOW':int,        'RINGA_MIN_SEC':int,     'RINGA_RED_SEC':int,     
                   'RINGA_YELLO_SEC':int,   'RINGB_FLOW':int,        'RINGB_MIN_SEC':int,     
                   'RINGB_RED_SEC':int,     'RINGB_YELLO_SEC':int,   'SAT_PLAN_NO':int,       
                   'SIGL_ANGLE':str,        'STOS_NO':int,           'SUN_PLAN_NO':int,       
                   'THU_PLAN_NO':int,       'TRFLIG_TYPE':int,       'TUE_PLAN_NO':int,       
                   'USE_YN':int,            'WED_PLAN_NO':int,       'adj_inc_edge_id':str,   
                   'adj_out_edge_id':str,   'child_id':str,          'condition':str,         
                   'inc_edge_id':str,       'inter_no':int,          'inter_type':int,        
                   'node_id':str,           'out_edge_id':str,       'parent_id':str,         
                   'phase_no':int,          'ring_type':str,         'turn_type':str}
loading_dtype_2 = {f'RING{alph}_PHASE{i}':int for alph in self.alphs for i in range(1,9)}
loading_dtype = {**loading_dtype_1, **loading_dtype_2}

# 테이블 불러오기

# 수작업으로 만든 테이블
self.inter_node = pd.read_csv(os.path.join(self.path_tables, 'inter_node.csv'), dtype=loading_dtype)
self.turn_type  = pd.read_csv(os.path.join(self.path_tables, 'turn_type.csv'), dtype=loading_dtype)
self.uturn      = pd.read_csv(os.path.join(self.path_tables, 'uturn.csv'), dtype=loading_dtype)
self.u_condition= pd.read_csv(os.path.join(self.path_tables, 'u_condition.csv'), dtype=loading_dtype)
self.coord      = pd.read_csv(os.path.join(self.path_tables, 'coord.csv'), dtype=loading_dtype)
self.turn_type  = pd.read_csv(os.path.join(self.path_tables, 'turn_type.csv'), dtype=loading_dtype)

# DB에서 fetch하는 테이블
self.dayplan    = pd.read_csv(os.path.join(self.path_tables, 'TC_IF_TOD_DAY_PLAN.csv'), dtype=loading_dtype)
self.holyplan   = pd.read_csv(os.path.join(self.path_tables, 'TC_IF_TOD_HOLIDAY_PLAN.csv'), dtype=loading_dtype)
self.red_yel    = pd.read_csv(os.path.join(self.path_tables, 'TC_IF_TOD_RED_YELLO.csv'), dtype=loading_dtype)
self.weekplan   = pd.read_csv(os.path.join(self.path_tables, 'TC_IF_TOD_WEEK_PLAN.csv'), dtype=loading_dtype)
self.history    = pd.read_csv(os.path.join(self.path_tables, 'TL_IF_SIGL_CYCL.csv'), dtype=loading_dtype)
self.inter_info = pd.read_csv(os.path.join(self.path_tables, 'TM_FA_CRSRD.csv'), dtype=loading_dtype)
self.angle      = pd.read_csv(os.path.join(self.path_tables, 'TN_IF_SIGL_FLOW.csv'), dtype=loading_dtype)

# 컬럼명 변경
rename_cname_1 = {'CRSRD_ID':'inter_no',      'CRSRD_NM':'inter_name',    'CRSRD_TYPE':'inter_type',  
                  'CYCL':'cycle',             'DAY':'DD',                 'FLOW_NO':'move_no',        
                  'GRP_NO':'group_no',        'HOUR':'hh',                'LGTD':'inter_lon',         
                  'LTTD':'inter_lat',         'MAIN_CRSRD_ID':'parent_id','MAIN_PHASE':'main_phase',  
                  'MIN':'mm',                 'MNTH':'MM',                'NODE_ID':'node_id',        
                  'OFFSET':'offset',          'PHASE':'phase_no',         'RING':'ring_type',         
                  'RINGA_RED_SEC':'red_A',    'RINGA_YELLO_SEC':'yel_A',  'RINGB_RED_SEC':'red_B',    
                  'RINGB_YELLO_SEC':'yel_B',  'SIGL_ANGLE':'angle_code',  'PLAN_NO':'plan_no'}

rename_cname_2 = {f'RING{alph}_PHASE{i}':f'dura_{alph}{i}' for alph in self.alphs for i in range(1,9)}
rename_cname = {**rename_cname_1, **rename_cname_2}

self.dayplan    = self.dayplan.rename(columns=rename_cname)
self.holyplan   = self.holyplan.rename(columns=rename_cname)
self.red_yel    = self.red_yel.rename(columns=rename_cname)
self.weekplan   = self.weekplan.rename(columns=rename_cname)
self.history    = self.history.rename(columns=rename_cname)
self.inter_info = self.inter_info.rename(columns=rename_cname)
self.angle      = self.angle.rename(columns=rename_cname)

# 교차로목록, 노드목록 정의
self.inter_nos = [int(x) for x in sorted(self.inter_info.inter_no.unique())]
self.node_ids = sorted(self.inter_node.node_id.unique())

In [22]:
# 1-3. 네트워크 무결성 검사
# (생략)

In [23]:
# 1-4. 테이블 무결성 검사
# (생략)

In [24]:
# 1-5. 주요 객체 (리스트, 딕셔너리) 저장

# 주교차로 / 부교차로 / 유턴교차로 / 연등교차로 노드id
self.parent_ids = sorted(self.inter_node[self.inter_node.inter_type==0].node_id.unique())
self.child_ids = sorted(self.inter_node[self.inter_node.inter_type==1].node_id.unique())
self.uturn_ids = sorted(self.uturn.node_id.unique())
self.coord_ids = sorted(self.coord.node_id.unique())

In [25]:
# 교차로번호 - 노드id 간 딕셔너리
self.node2inter = dict(zip(self.inter_node['node_id'], self.inter_node['inter_no']))
self.inter2nodes = {inter:[key for key, value in self.node2inter.items() if value == inter] for inter in self.node2inter.values()}
self.inter2node = dict(zip(self.inter_node[self.inter_node.inter_type==0]['inter_no'], self.inter_node[self.inter_node.inter_type==0]['node_id']))
self.node2type = dict(zip(self.inter_node['node_id'], self.inter_node['inter_type']))
# 주교차로id - 부교차로id 간 딕셔너리
self.child2parent = dict()
for child_id in list(self.inter_node[self.inter_node.inter_type==1]['node_id'].unique()):
    inter_no = self.inter_node[self.inter_node.node_id==child_id].iloc[0].inter_no
    parent_id = self.inter_node[self.inter_node.inter_no==inter_no][self.inter_node[self.inter_node.inter_no==inter_no].inter_type==0].iloc[0].node_id
    self.child2parent[child_id] = parent_id
self.parent2childs = {parent_id:[key for key, value in self.child2parent.items() if value == parent_id] for parent_id in self.child2parent.values()}

In [26]:
# 1-6. 신호계획 테이블 통합

now = datetime.datetime.now()
# 월, 일
MM, DD, hh, mm = now.month, now.day, now.hour, now.minute
hplan = self.holyplan[(self.holyplan.MM==MM) & (self.holyplan.DD==DD)]

# 요일
dow_number = now.weekday()
dows = [dow for dow in self.weekplan.columns if dow.endswith('PLAN_NO')]
dows = dows[1:] + dows[0:1]
dow = dows[dow_number]

# 오늘에 해당하는 신호계획 추출
if len(hplan):
    # (inter_no, plan_no) 목록 
    inter_pnos = list(zip(hplan['inter_no'], hplan['plan_no']))
else:
    inter_pnos = list(zip(self.weekplan.inter_no, self.weekplan[dow]))

# 통합된 테이블 (오늘)
self.plan = self.dayplan.copy()
self.plan['inter_pno'] = list(zip(self.plan['inter_no'], self.plan['plan_no']))
self.plan = self.plan[(self.plan.inter_pno.isin(inter_pnos))]
self.plan = self.plan.drop(columns='inter_pno')
self.plan.head()

inter_no  plan_no  hh  mm  cycle  offset  dura_A1  dura_A2  dura_A3  \
0       175        1   0   0    160      57       37       39       55   
1       175        1   7   0    170      40       40       42       55   
2       175        1   9   0    180      28       43       45       55   
3       175        1  18  30    190      18       46       48       55   
4       176        1   0   0    150     131       37       73       40   

   dura_A4  ...  dura_A8  dura_B1  dura_B2  dura_B3  dura_B4  dura_B5  \
0       29  ...        0       37       39       25       59        0   
1       33  ...        0       40       42       29       59        0   
2       37  ...        0       43       45       33       59        0   
3       41  ...        0       46       48       37       59        0   
4        0  ...        0       37       73       40        0        0   

   dura_B6  dura_B7  dura_B8               LAST_MDFCN_DT  
0        0        0        0  2024-07-12 16:36:43.702267  
1        0        0        0  2024-07-12 16:36:43.702267  
2        0        0        0  2024-07-12 16:36:43.702267  
3        0        0        0  2024-07-12 16:36:43.702267  
4        0        0        0  2024-07-12 16:36:43.702267  

[5 rows x 23 columns]

In [27]:
# angle 테이블에서 필요없는 현시번호 제거
self.angle_new = []
for inter_no in self.inter_nos:
    ang = self.angle[self.angle.inter_no==inter_no]
    max_phase_no = ang.dropna(subset='angle_code')['phase_no'].max()
    self.angle_new.append(ang[ang.phase_no <= max_phase_no])
self.angle = pd.concat(self.angle_new)

In [28]:
# 노드id 생성
self.angle['node_id'] = self.angle['inter_no'].map(self.inter2node)
# 주교차로id 생성
self.angle['parent_id'] = self.angle['node_id']
# 불필요컬럼 제거
self.angle = self.angle.drop(columns='move_no')
# 진입/진출 엣지id 지정
for index, row in self.angle.iterrows():
    node_id = row.node_id
    if not isinstance(row.angle_code, str) or len(row.angle_code)!=6:
        continue
    # 방위각
    inc_angle = int(row.angle_code[:3])
    out_angle = int(row.angle_code[3:])
    self.angle.at[index, 'inc_angle'] = inc_angle
    self.angle.at[index, 'out_angle'] = out_angle
    # 일반각 및 라디안으로 변환, 실제 방향 설정
    inc_angle = (90 - inc_angle) % 360
    inc_angle = inc_angle * np.pi / 180
    inc_vec_true = np.array([np.cos(inc_angle), np.sin(inc_angle)])
    out_angle = (90 - out_angle) % 360
    out_angle = out_angle * np.pi / 180
    out_vec_true = np.array([np.cos(out_angle), np.sin(out_angle)])

    # 진입로 목록
    inc_edge_ids = [edge.getID() for edge in self.net.getNode(node_id).getIncoming()]
    inc_vecs = []
    for inc_edge_id in inc_edge_ids:
        init_pt = self.net.getEdge(inc_edge_id).getShape()[-1]
        term_pt = self.net.getEdge(inc_edge_id).getShape()[-2]
        assert init_pt != term_pt
        inc_vec = np.array(term_pt) - np.array(init_pt)
        inc_vec = inc_vec / np.linalg.norm(inc_vec)
        inc_vecs.append(inc_vec)
    # 각도에 맞는 진입로 지정
    max_index = np.argmax([np.dot(inc_vec, inc_vec_true) for inc_vec in inc_vecs])
    inc_edge_id = inc_edge_ids[max_index]
    self.angle.at[index, 'inc_edge_id'] = inc_edge_id

    # 진출로 목록
    out_edge_ids = [edge.getID() for edge in self.net.getNode(node_id).getOutgoing()]
    out_vecs = []
    for out_edge_id in out_edge_ids:
        init_pt = self.net.getEdge(out_edge_id).getShape()[0]
        term_pt = self.net.getEdge(out_edge_id).getShape()[1]
        assert init_pt != term_pt
        out_vec = np.array(term_pt) - np.array(init_pt)
        out_vec = out_vec / np.linalg.norm(out_vec)
        out_vecs.append(out_vec)
    # 각도에 맞는 진출로 지정
    max_index = np.argmax([np.dot(out_vec, out_vec_true) for out_vec in out_vecs])
    out_edge_id = out_edge_ids[max_index]
    self.angle.at[index, 'out_edge_id'] = out_edge_id
# matcher로 테이블명 변경
self.matcher = self.angle.drop(columns='angle_code')

In [29]:
# turn_type 지정
io2turn_type = dict()
for row in self.turn_type.itertuples():
    if not (row.inc_edge_id, row.out_edge_id) in io2turn_type:
        io2turn_type[(row.inc_edge_id, row.out_edge_id)] = row.turn_type
    else:
        if io2turn_type[(row.inc_edge_id, row.out_edge_id)] != row.turn_type:
            print('the dictionary is not well-defined')
self.matcher['turn_type'] = self.matcher.apply(lambda row:io2turn_type.get((row['inc_edge_id'], row['out_edge_id']), None), axis=1)
self.matcher['turn_type'] = self.matcher['turn_type'].map({'straight': 'S', 'left': 'L', 'right': 'R'})
# node_type 지정
self.matcher['node_type'] = 'normal'

In [30]:
# 유턴조건 관련 객체 정의
self.angle_sep = 20
u_condition = dict(zip(self.u_condition.child_id, self.u_condition.condition))

# (노드id, 진입엣지) 별 각도
NIA = [] # (node_id, inc_edge_id, angle)
NIs = set(zip(self.matcher.node_id, self.matcher.inc_edge_id)) # (node_id, inc_edge_id)
NIs = sorted(ni for ni in NIs if not pd.isna(ni[1]))
for node_id, inc_edge_id in NIs:
    ang = self.matcher[(self.matcher.node_id==node_id) & (self.matcher.inc_edge_id==inc_edge_id)]
    mean_x = np.mean(np.cos(np.deg2rad(ang.inc_angle)))
    mean_y = np.mean(np.sin(np.deg2rad(ang.inc_angle)))
    mean_angle = int(np.rad2deg(np.arctan2(mean_y, mean_x)) % 360)
    NIA.append(pd.DataFrame({'node_id':[node_id], 'inc_edge_id':[inc_edge_id], 'angle':[mean_angle]}))
NIA = pd.concat(NIA).reset_index(drop=True)

# (노드id, 진출엣지) 별 각도
NOA = [] # (node_id, out_edge_id, angle)
NOs = set(zip(self.matcher.node_id, self.matcher.out_edge_id)) # (node_id, out_edge_id)
NOs = sorted(no for no in NOs if not pd.isna(no[1]))
for node_id, out_edge_id in NOs:
    ang = self.matcher[(self.matcher.node_id==node_id) & (self.matcher.out_edge_id==out_edge_id)]
    mean_x = np.mean(np.cos(np.deg2rad(ang.out_angle)))
    mean_y = np.mean(np.sin(np.deg2rad(ang.out_angle)))
    mean_angle = int(np.rad2deg(np.arctan2(mean_y, mean_x)) % 360)
    NOA.append(pd.DataFrame({'node_id':[node_id], 'out_edge_id':[out_edge_id], 'angle':[mean_angle]}))
NOA = pd.concat(NOA).reset_index(drop=True)

In [31]:
uangles = []
for uturn_id in self.uturn_ids:
    parent_id = self.child2parent[uturn_id] # 주교차로 노드id
    condition = u_condition[uturn_id] # 유턴조건
    # 바꿔서 넣을 데이터프레임
    uangle = self.matcher[self.matcher.parent_id==parent_id].copy() # 'angle' dataframe for a specific 'parent_id'
    uangle['node_id'] = uturn_id
    uangle['node_type'] = 'uturn'
    # 유턴에 관한 정보
    urow = self.uturn[self.uturn.node_id==uturn_id].iloc[0]
    node_id = urow.parent_id
    inc_edge_id = urow.inc_edge_id # 유턴 진입엣지id
    out_edge_id = urow.out_edge_id # 유턴 진출엣지id
    adj_inc_edge_id = urow.adj_inc_edge_id # 유턴 인접진입엣지id
    adj_out_edge_id = urow.adj_out_edge_id # 유턴 인접진출엣지id

    # 해당 노드에 대한 (노드id, 진입(출)엣지id, 방위각) 데이터프레임
    nia = NIA[NIA.node_id==node_id].sort_values(by='angle').reset_index(drop=True)
    noa = NOA[NOA.node_id==node_id].sort_values(by='angle').reset_index(drop=True)

    # 진입엣지 각도
    inc_angle = nia[nia.inc_edge_id==adj_inc_edge_id].iloc[0].angle

    # 진/출입로 각도 목록 (extended)
    inc_angles = np.array(nia.angle)
    inc_angles = np.concatenate((inc_angles - 360, inc_angles, inc_angles + 360))
    out_angles = np.array(noa.angle)
    out_angles = np.concatenate((out_angles - 360, out_angles, out_angles + 360))

    # 좌측 진출로 (좌회전신호시 진출로)
    out_angles_left = out_angles[out_angles >= inc_angle + self.angle_sep]
    out_angle_left = np.sort(out_angles_left)[0] % 360
    out_edge_id_left = noa[noa.angle==out_angle_left].iloc[0].out_edge_id

    # 좌측 진입로 (보행신호시 진입로)
    inc_angles_left = inc_angles[inc_angles >= inc_angle + self.angle_sep]
    inc_angle_left = np.sort(inc_angles_left)[0] % 360
    inc_edge_id_left = nia[nia.angle==inc_angle_left].iloc[0].inc_edge_id

    # 우측 진출로 (보행신호시 진출로)
    out_angles_right = out_angles[out_angles <= inc_angle - self.angle_sep]
    out_angle_right = np.sort(out_angles_right)[-1] % 360
    out_edge_id_right = noa[noa.angle==out_angle_right].iloc[0].out_edge_id

    # 좌회전시 조건
    left_flag = (uangle.inc_edge_id==adj_inc_edge_id) & (uangle.out_edge_id==out_edge_id_left) & (uangle.turn_type=='L')

    # 보행신호시 조건
    pedes_flag = (uangle.inc_edge_id==inc_edge_id_left) & (uangle.out_edge_id==out_edge_id_right)

    # 진출엣지가 유턴 인접진출엣지와 다르다는 조건
    out_adj_coincides = uangle[uangle.out_edge_id==adj_out_edge_id]
    out_adj_flag = ~uangle.phase_no.isin(out_adj_coincides.phase_no)

    if condition == '좌회전시':
        # 유턴교차로에 대한 from / to 재입력
        uangle.loc[left_flag, ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]
        uangle.loc[~left_flag, ['inc_edge_id', 'out_edge_id']] = ['', '']

    elif condition == '보행신호시':
        # 유턴교차로에 대한 from / to 재입력
        uangle.loc[pedes_flag, ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]
        uangle.loc[~pedes_flag, ['inc_edge_id', 'out_edge_id']] = ['', '']

    uturn_not_assigned = (uangle[['inc_edge_id', 'out_edge_id']] == ('', '')).any(axis=1).all()
    if uturn_not_assigned:
        if left_flag.any():
            uangle.loc[left_flag, ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]
            uangle.loc[~left_flag, ['inc_edge_id', 'out_edge_id']] = ['', '']
        elif pedes_flag.any():
            uangle.loc[left_flag, ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]
            uangle.loc[~left_flag, ['inc_edge_id', 'out_edge_id']] = ['', '']
        elif out_adj_flag.any():
            uangle.loc[out_adj_flag, ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]
            uangle.loc[~out_adj_flag, ['inc_edge_id', 'out_edge_id']] = ['', '']
    uangles.append(uangle)

In [32]:
# 연등교차로 처리
self.coord[['inc_edge_id', 'out_edge_id']] = self.coord[['inc_edge_id', 'out_edge_id']].fillna('')
self.coord['node_type'] = 'coord'
self.coord

inter_no parent_id node_id  STOS_NO  phase_no ring_type      inc_edge_id  \
0       178        i3     c30        0         1         A                    
1       178        i3     c30        0         1         B                    
2       178        i3     c30        0         2         A     571542116_01   
3       178        i3     c30        0         2         B  571542116_02.96   
4       178        i3     c30        0         3         A     571542116_01   
5       178        i3     c30        0         3         B  571542116_02.96   
6       178        i3     c30        0         4         A     571542116_01   
7       178        i3     c30        0         4         B  571542116_02.96   

        out_edge_id turn_type node_type  
0                         NaN     coord  
1                         NaN     coord  
2  -571542116_02.96         S     coord  
3  571542116_02.164         S     coord  
4  -571542116_02.96         S     coord  
5  571542116_02.164         S     coord  
6  -571542116_02.96         S     coord  
7  571542116_02.164         S     coord

In [33]:
self.matcher = pd.concat([self.matcher, *uangles, self.coord])
self.matcher = self.matcher.drop(columns=['inc_angle', 'out_angle'])
self.matcher[:60]

inter_no  phase_no ring_type  STOS_NO node_id parent_id  \
0         175         1         A        0      i0        i0   
1         175         1         B        0      i0        i0   
2         175         2         A        0      i0        i0   
3         175         2         B        0      i0        i0   
4         175         3         A        0      i0        i0   
5         175         3         B        0      i0        i0   
6         175         4         A        0      i0        i0   
7         175         4         B        0      i0        i0   
16        176         1         A        0      i1        i1   
17        176         1         B        0      i1        i1   
18        176         2         A        0      i1        i1   
19        176         2         B        0      i1        i1   
20        176         3         A        0      i1        i1   
21        176         3         B        0      i1        i1   
32        177         1         A        0      i2        i2   
33        177         1         B        0      i2        i2   
34        177         2         A        0      i2        i2   
35        177         2         B        0      i2        i2   
36        177         3         A        0      i2        i2   
37        177         3         B        0      i2        i2   
38        177         4         A        0      i2        i2   
39        177         4         B        0      i2        i2   
48        178         1         A        0      i3        i3   
49        178         1         B        0      i3        i3   
50        178         2         A        0      i3        i3   
51        178         2         B        0      i3        i3   
52        178         3         A        0      i3        i3   
53        178         3         B        0      i3        i3   
54        178         4         A        0      i3        i3   
55        178         4         B        0      i3        i3   
64        201         1         A        0      i8        i8   
65        201         1         B        0      i8        i8   
66        201         2         A        0      i8        i8   
67        201         2         B        0      i8        i8   
68        201         3         A        0      i8        i8   
69        201         3         B        0      i8        i8   
70        201         4         A        0      i8        i8   
71        201         4         B        0      i8        i8   
72        201         5         A        0      i8        i8   
73        201         5         B        0      i8        i8   
80        202         1         A        0      i9        i9   
81        202         1         B        0      i9        i9   
82        202         2         A        0      i9        i9   
83        202         2         B        0      i9        i9   
96        206         1         A        0      i7        i7   
97        206         1         B        0      i7        i7   
98        206         2         A        0      i7        i7   
99        206         2         B        0      i7        i7   
100       206         3         A        0      i7        i7   
101       206         3         B        0      i7        i7   
102       206         4         A        0      i7        i7   
103       206         4         B        0      i7        i7   
112       210         1         A        0      i6        i6   
113       210         1         B        0      i6        i6   
114       210         2         A        0      i6        i6   
115       210         2         B        0      i6        i6   
116       210         3         A        0      i6        i6   
117       210         3         B        0      i6        i6   
118       210         4         A        0      i6        i6   
119       210         4         B        0      i6        i6   

          inc_edge_id       out_edge_id turn_type node_type  
0       -571542797_02      571500487_0